In [80]:
import numpy as np
import gurobipy as gb
import networkx as nx
import matplotlib.pyplot as plt

## 1-Dollo problem -- complete specification

In [194]:
FORBIDDEN = [
    # condition 1
    [[1,0],[0,1],[1,1]],
    [[1,0],[0,1],[1,2]],
    [[1,0],[0,2],[1,1]],
    [[1,0],[0,2],[1,2]],
    [[1,0],[0,1],[2,1]],
    [[1,0],[0,1],[2,2]],
    [[1,0],[0,2],[2,1]],
    [[1,0],[0,2],[2,2]],
    [[2,0],[0,1],[1,1]],
    [[2,0],[0,1],[1,2]],
    [[2,0],[0,2],[1,1]],
    [[2,0],[0,2],[1,2]],
    [[2,0],[0,1],[2,1]],
    [[2,0],[0,1],[2,2]],
    [[2,0],[0,2],[2,1]],
    [[2,0],[0,2],[2,2]],
    # condition 2
    [[1,1],[0,2],[1,2]],
    [[1,1],[0,2],[2,2]],
    [[2,1],[0,2],[1,2]],
    [[2,1],[0,2],[2,2]],
    # condition 3
    [[2,0],[1,1],[2,1]],
    [[2,0],[1,1],[2,2]],
    [[2,0],[1,2],[2,1]],
    [[2,0],[1,2],[2,2]],
    # condition 4
    [[2,1],[1,2],[2,2]]
]

In [175]:
def flatten(m, n, p, c, i):
    return p * n * 3 + c * 3 + i
    
def createILP(B, complete=True):
    """
    Create the ILP model given binary matrix B

    Parameters:
        B (np.array): Binary matrix B
        complete (bool): Indicates whether to include forbidden submatrix constraints

    Returns:
        gurobipy.Model: Gurobi ILP model
    """
    model = gb.Model("1-Dollo")
    m = B.shape[0]
    n = B.shape[1]

    a = model.addVars(range(m*n*3), vtype=gb.GRB.BINARY)
    for p in range(m):
        for c in range(n):
            for i in range(3):
                a[flatten(m, n, p, c, i)].varName = "a_" + str(p) + "_" + str(c) + "_" + str(i)
                model.addConstr(gb.quicksum(a[flatten(m, n, p, c, i)] for i in range(3)) == 1)
                model.addConstr(a[flatten(m, n, p, c, 1)] == B[p, c])

    if complete:
        for p in range(m):
            for q in range(m):
                if p == q: continue
                for r in range(m):
                    if q == r or p == r: continue
                    for c in range(n):
                        for d in range(n):
                            if c == d: continue
    
                            for idx in range(len(FORBIDDEN)):
                                model.addConstr(a[flatten(m, n, p, c, FORBIDDEN[idx][0][0])] + 
                                                a[flatten(m, n, p, d, FORBIDDEN[idx][0][1])] +
                                                a[flatten(m, n, q, c, FORBIDDEN[idx][1][0])] + 
                                                a[flatten(m, n, q, d, FORBIDDEN[idx][1][1])] +
                                                a[flatten(m, n, r, c, FORBIDDEN[idx][2][0])] + 
                                                a[flatten(m, n, r, d, FORBIDDEN[idx][2][1])] <= 5)

    model.setObjective(gb.quicksum(a[flatten(m, n, p, c, 2)] for p in range(m) for c in range(n)), gb.GRB.MINIMIZE)
    
    model.update()
    return model

In [83]:
B = np.array([[1,1,0,1], [0,1,0,1], [1,0,0,1], [0,0,1,0]])

In [84]:
model = createILP(B)

In [85]:
model.optimize()

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[rosetta2])

CPU model: Apple M1 Max
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 7296 rows, 48 columns and 43392 nonzeros
Model fingerprint: 0x4b8362b2
Variable types: 0 continuous, 48 integer (48 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 5e+00]
Found heuristic solution: objective 1.0000000
Presolve removed 7296 rows and 48 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.02 seconds (0.01 work units)
Thread count was 1 (of 10 available processors)

Solution count 1: 1 

Optimal solution found (tolerance 1.00e-04)
Best objective 1.000000000000e+00, best bound 1.000000000000e+00, gap 0.0000%


In [86]:
def extractSolution(model, m, n, verbose=False):
    """
    Extract solution tree from solved model

    Parameters:
        model (gurobipy.Model): Gurobi ILP model
        verbose (bool): Printing of variables to stdout

    Returns:
        gurobipy.Model: Gurobi ILP model
    """
    A = np.zeros((m, n), dtype=int)
    for idx, v in enumerate(model.getVars()):
        if v.Xn > 0.5:
            if verbose:
                print(v.varName, v.Xn)
            if v.varName.startswith("a"):
                s = v.varName.split("_")
                p = int(s[1])
                c = int(s[2])
                i = int(s[3])
                A[p,c] = i
    return A

In [87]:
extractSolution(model, B.shape[0], B.shape[1], verbose=False)

array([[1, 1, 0, 1],
       [0, 1, 0, 1],
       [1, 2, 0, 1],
       [0, 0, 1, 0]])

In [88]:
B

array([[1, 1, 0, 1],
       [0, 1, 0, 1],
       [1, 0, 0, 1],
       [0, 0, 1, 0]])

In [89]:
model.write("test.lp")

In [118]:
B_large = np.loadtxt("m25_n25_s1_k1_loss0.4.B", delimiter=" ", skiprows=2, dtype=int)

In [119]:
B_large[:10,:10]

array([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 1, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 1, 0, 0, 0, 1, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 1, 0, 0, 0, 0, 1, 0, 0],
       [0, 0, 0, 1, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 1]])

In [126]:
model_large = createILP(B_large[:11,:20])

In [127]:
model_large.optimize()

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[rosetta2])

CPU model: Apple M1 Max
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 9406320 rows, 660 columns and 56432640 nonzeros
Model fingerprint: 0xc14e3e30
Variable types: 0 continuous, 660 integer (660 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 5e+00]
Found heuristic solution: objective 75.0000000
Presolve removed 0 rows and 0 columns (presolve time = 5s) ...
Presolve removed 9082638 rows and 220 columns (presolve time = 11s) ...
Presolve removed 9083208 rows and 470 columns (presolve time = 15s) ...
Presolve removed 9245244 rows and 470 columns (presolve time = 20s) ...
Presolve removed 9245244 rows and 470 columns (presolve time = 25s) ...
Presolve removed 9245244 rows and 470 columns (presolve time = 30s) ...
Presolve removed 9245244 rows and 470 colum

In [122]:
extractSolution(model_large, 10, 10)

array([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 1, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 1, 0, 0, 0, 1, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
       [0, 0, 1, 0, 0, 0, 0, 1, 0, 0],
       [0, 0, 0, 1, 0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 1]])

In [140]:
B_large[np.ix_((1,3,2),(1,2,5,6,7,3))]

array([[0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0]])

## 1-Dollo problem -- Cutting Planes (naively)

In [176]:
def solveManualBC(model, m, n):
    while True:
        model.optimize()
        
        if model.status in (gb.GRB.INF_OR_UNBD, gb.GRB.INFEASIBLE, gb.GRB.UNBOUNDED):
            break

        A = extractSolution(model, m, n)
        update = False
    
        for p in range(m):
            for q in range(m):
                if p == q: continue
                for r in range(m):
                    if q == r or p == r: continue
                    for c in range(n):
                        for d in range(n):
                            if c == d: continue
    
                            for idx in range(len(FORBIDDEN)):
                                if A[p,c] == FORBIDDEN[idx][0][0] \
                                    and A[p,d] == FORBIDDEN[idx][0][1] \
                                    and A[q,c] == FORBIDDEN[idx][1][0] \
                                    and A[q,d] == FORBIDDEN[idx][1][1] \
                                    and A[r,c] == FORBIDDEN[idx][2][0] \
                                    and A[r,d] == FORBIDDEN[idx][2][1]:
                                    model.addConstr(model.getVars()[flatten(m, n, p, c, FORBIDDEN[idx][0][0])] + 
                                                    model.getVars()[flatten(m, n, p, d, FORBIDDEN[idx][0][1])] +
                                                    model.getVars()[flatten(m, n, q, c, FORBIDDEN[idx][1][0])] + 
                                                    model.getVars()[flatten(m, n, q, d, FORBIDDEN[idx][1][1])] +
                                                    model.getVars()[flatten(m, n, r, c, FORBIDDEN[idx][2][0])] + 
                                                    model.getVars()[flatten(m, n, r, d, FORBIDDEN[idx][2][1])] <= 5)
                                    update = True
        if update:
            model.update()
        else:
            break


In [182]:
%%timeit
model_large2 = createILP(B_large, False)

51 ms ± 283 µs per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [183]:
%%timeit
solveManualBC(model_large2, 25, 25)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[rosetta2])

CPU model: Apple M1 Max
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 3870 rows, 1875 columns and 8220 nonzeros
Model fingerprint: 0x51584048
Variable types: 0 continuous, 1875 integer (1875 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 5e+00]
Presolved: 4 rows, 4 columns, 8 nonzeros

Continuing optimization...


Explored 1 nodes (0 simplex iterations) in 0.01 seconds (0.00 work units)
Thread count was 10 (of 10 available processors)

Solution count 2: 2 278 

Optimal solution found (tolerance 1.00e-04)
Best objective 2.000000000000e+00, best bound 2.000000000000e+00, gap 0.0000%
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[rosetta2])

CPU model: Apple M1 Max
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Op

In [178]:
extractSolution(model_large2, 25, 25)

array([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1,
        1, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0,
        0, 1, 0],
       [0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
      

In [179]:
B_large

array([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1,
        1, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
        0, 0, 0],
       [0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0,
        0, 1, 0],
       [0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0,
        0, 0, 0],
       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
      

## 1-Dollo problem -- Cutting Planes (callback)

In [191]:
def forbidden_matrix_cb(model, where):
    if where == gb.GRB.Callback.MIPSOL:
        vals = model.cbGetSolution(model.getVars())
        m=25
        n=25
        for p in range(m):
            for q in range(m):
                if p == q: continue
                for r in range(m):
                    if q == r or p == r: continue
                    for c in range(n):
                        for d in range(n):
                            if c == d: continue
    
                            for idx in range(len(FORBIDDEN)):
                                if vals[flatten(m, n, p, c, FORBIDDEN[idx][0][0])] > 0.5 \
                                    and vals[flatten(m, n, p, d, FORBIDDEN[idx][0][1])] > 0.5 \
                                    and vals[flatten(m, n, q, c, FORBIDDEN[idx][1][0])] > 0.5 \
                                    and vals[flatten(m, n, q, d, FORBIDDEN[idx][1][1])] > 0.5 \
                                    and vals[flatten(m, n, r, c, FORBIDDEN[idx][2][0])] > 0.5 \
                                    and vals[flatten(m, n, r, d, FORBIDDEN[idx][2][1])] > 0.5:
                                    model.cbLazy(model.getVars()[flatten(m, n, p, c, FORBIDDEN[idx][0][0])] + 
                                                    model.getVars()[flatten(m, n, p, d, FORBIDDEN[idx][0][1])] +
                                                    model.getVars()[flatten(m, n, q, c, FORBIDDEN[idx][1][0])] + 
                                                    model.getVars()[flatten(m, n, q, d, FORBIDDEN[idx][1][1])] +
                                                    model.getVars()[flatten(m, n, r, c, FORBIDDEN[idx][2][0])] + 
                                                    model.getVars()[flatten(m, n, r, d, FORBIDDEN[idx][2][1])] <= 5)

In [192]:
model_large2 = createILP(B_large, False)

In [193]:
model_large2.Params.LazyConstraints = 1
model_large2.optimize(forbidden_matrix_cb)

Set parameter LazyConstraints to value 1
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[rosetta2])

CPU model: Apple M1 Max
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 3750 rows, 1875 columns and 7500 nonzeros
Model fingerprint: 0x083bcb5e
Variable types: 0 continuous, 1875 integer (1875 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Presolve removed 3750 rows and 1329 columns
Presolve time: 0.00s
Presolved: 0 rows, 546 columns, 0 nonzeros
Variable types: 0 continuous, 546 integer (546 binary)

Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    2.0000000e+00   0.000000e+00   0.000000e+00    130s

Root relaxation: objective 2.000000e+00, 0 iterations, 0.00 seconds (0.00 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 E